In [132]:
import pyodbc
import configparser
import pandas as pd
import numpy as np 
from datetime import datetime, time


config = configparser.ConfigParser()
config.read(r"C:\Users\joao.herculano\GRUPO GINSENG\Assistência Suprimentos - 2025\CODIGOS\relatório_improdutivo\credenciais.ini")

# Conexão com o banco
conn = pyodbc.connect(
    f"DRIVER={{SQL Server}};"
    f"SERVER={config['banco']['host']},1433;"
    f"DATABASE=GINSENG;"
    f"UID={config['banco']['user']};"
    f"PWD={config['banco']['password']}")

#gerar query
query = '''
SELECT 
    e.pdv,
    e.SKU,
    COALESCE(e.SKU_PARA, e.SKU) AS SKU_FINAL,
    MAX(e.[ESTOQUE ATUAL]) AS [ESTOQUE ATUAL],
    MAX(e.[ESTOQUE EM TRANSITO]) AS [ESTOQUE EM TRANSITO],
    MAX(e.[PEDIDO PENDENTE]) AS [PEDIDO PENDENTE],
    d.salescurve AS Curva,
    e.CATEGORIA,
    d.dayswithoutsales AS DiasSemVenda,
    d.nextcycleprojection,
    d.secondtonextcycleprojection
FROM 
    estoque_mar e  
LEFT JOIN draft d 
    ON d.loja_id = e.PDV 
   AND d.code = COALESCE(e.SKU_PARA, e.SKU)
WHERE 
    d.businessunit = 'EUD'
GROUP BY 
    e.pdv,
    e.SKU,
    COALESCE(e.SKU_PARA, e.SKU),
    d.salescurve,
    e.CATEGORIA,
    d.dayswithoutsales,
    d.nextcycleprojection,
    d.secondtonextcycleprojection
'''
df0 = pd.read_sql(query, conn)



C:\Users\joao.herculano\AppData\Local\Temp\ipykernel_41628\2131003807.py:50: UserWarning: pandas only supports SQLAlchemy connectable (engine/connection) or database string URI or sqlite3 DBAPI2 connection. Other DBAPI2 objects are not tested. Please consider using SQLAlchemy.
  df0 = pd.read_sql(query, conn)


In [279]:
df0[(df0['SKU'] == '93403') & (df0['pdv'] == 21375)]

Empty DataFrame
Columns: [pdv, SKU, SKU_FINAL, ESTOQUE ATUAL, ESTOQUE EM TRANSITO, PEDIDO PENDENTE, Curva, CATEGORIA, DiasSemVenda, nextcycleprojection, secondtonextcycleprojection]
Index: []

In [134]:
query_vendas = '''
SELECT 
	B.PDV, 
	B.SKU,
	B.DESCRICAO,
	SUM(CAST(b.VENDAS AS DECIMAL(18,2))) AS VENDAS_CICLO,
	C.Ciclo
FROM base_vendas_bi b
INNER JOIN ciclos_data_2025 c 
    ON CAST(b.[DATA] AS DATE) = CONVERT(DATE, c.[Date], 103) AND C.MARCA = 'BOT'
LEFT JOIN (
    SELECT SKU, MAX(ORIGEM) AS ORIGEM
    FROM estoque_mar
    GROUP BY SKU
) e ON b.SKU = e.SKU
WHERE b.[DATA] > '2024-07-28'
GROUP BY
B.PDV, 
	B.SKU,
	B.DESCRICAO,
	C.Ciclo,
	E.ORIGEM 
'''

dfv0 = pd.read_sql(query_vendas, conn)

conn.close()

C:\Users\joao.herculano\AppData\Local\Temp\ipykernel_41628\1692316838.py:25: UserWarning: pandas only supports SQLAlchemy connectable (engine/connection) or database string URI or sqlite3 DBAPI2 connection. Other DBAPI2 objects are not tested. Please consider using SQLAlchemy.
  dfv0 = pd.read_sql(query_vendas, conn)


In [135]:
df=df0

In [136]:
dfv0.head()

PDV    SKU                               DESCRICAO  VENDAS_CICLO    Ciclo
0  12823  48664     BOTICOLL PORTINARI DES COL 100ml V5           1.0  C202411
1  12826  48060      LILY CREM DES HID ACET CPO 250g V8           7.0  C202414
2  20998  55142  CASA 214 DIFUS VARET BRIS/CEDROS 250ml           1.0  C202414
3  21495  52225           NSPA SAB BARR CPO AMEI 90g V6           0.0  C202412
4  20441  52016        NSPA CREM HID MAOS AMEI DOUR 75g           1.0  C202413

In [137]:

# 1. Agrupamento
df_agrupado = dfv0.groupby(['PDV', 'SKU', 'DESCRICAO', 'Ciclo'], as_index=False)['VENDAS_CICLO'].sum()

# 2. Pivotar o DataFrame
df_pivotado = df_agrupado.pivot_table(
    index=['PDV', 'SKU', 'DESCRICAO'],
    columns='Ciclo',
    values='VENDAS_CICLO',
    fill_value=0  # Substitui NaN por 0
)

# 3. Resetar o índice para deixar como DataFrame normal (opcional)
df_vendas = df_pivotado.reset_index()

# 4. (Opcional) Renomear colunas com prefixo "Ciclo_"
df_vendas.columns.name = None
df_vendas = df_vendas.rename(columns=lambda x: f'Ciclo_{x}' if isinstance(x, (int, str)) and str(x).isdigit() else x)

# Resultado final
df_vendas.head()


PDV   SKU                            DESCRICAO  C202411  C202412  \
0  11201  1004        FLORATTA DES COL MY BLUE 75ml      0.0      0.0   
1  11201  1005     DEM FLORATTA DES COL MY BLUE 4ml      0.0      0.0   
2  11201  1078      MATCH SRUM CAP POS QUIMICA 50ml      0.0      0.0   
3  11201  1296  PMPCK THE BLEND DES ANTIT AER 2x75g      0.0      0.0   
4  11201  1302       PMPCK LILY DES ANTIT AER 2x75g      0.0      0.0   

   C202413  C202414  C202415  C202416  C202417  ...  C202503  C202504  \
0      0.0      0.0      0.0      0.0      0.0  ...      0.0      0.0   
1      0.0      0.0      0.0      0.0      0.0  ...      0.0      0.0   
2      0.0      0.0      0.0      0.0      0.0  ...      0.0      0.0   
3      0.0      0.0      0.0      0.0      0.0  ...      0.0      0.0   
4      0.0      0.0      0.0      0.0      0.0  ...      0.0      0.0   

   C202505  C202506  C202507  C202508  C202509  C202510  C202511  C202512  
0      0.0      0.0      0.0      0.0      0.0      0.0      0.0      0.0  
1      0.0      0.0      0.0      0.0      0.0      0.0      0.0      0.0  
2      0.0      0.0      0.0      0.0      0.0      0.0      0.0      0.0  
3      0.0      0.0      0.0      0.0      0.0      0.0      0.0      0.0  
4      0.0      0.0      0.0      0.0      0.0      0.0      0.0      0.0  

[5 rows x 22 columns]

In [138]:
# O QUE PRECISA PRA RODAR ESSE CÓDIGO:

# Arquivo Draft
# Arquivo Estoque
# Arquivo BI preço
# Arquivo pdv
# Arquivo Calendario
# Arquivo tabela de compra

#Atualizar o nome da marca no filtro do estoque.

In [139]:
# Caminho onde estão as subpastas com os arquivos CSV

# Set the path to the folder containing CSV files
#folder_path = r"C:\Users\joao.herculano\GRUPO GINSENG\Assistência Suprimentos - 2025\SUPRIMENTOS\BD_LANÇAMENTOS\EUDORA\C13\DRAFT"   # arquivo dos drafts

# Pattern to match all CSV files
#csv_files = glob.glob(os.path.join(folder_path, '*.csv'))

# Read and concat all CSVs
#df_draft = pd.concat([pd.read_csv(file) for file in csv_files], ignore_index=True)


#df_draft.shape


In [140]:


#Caminho onde estão as subpastas com os arquivos CSV
#pasta_entrada =  r"C:\Users\joao.herculano\GRUPO GINSENG\Assistência Suprimentos - 2025\SUPRIMENTOS\BD_LANÇAMENTOS\EUDORA\C13\estoque"

# Lista todas as subpastas dentro de "ESTOQUE"
#subpastas = [os.path.join(pasta_entrada, d) for d in os.listdir(pasta_entrada) if os.path.isdir(os.path.join(pasta_entrada, d))]

#df_list = []

# Percorre todas as subpastas
#for subpasta in subpastas:
#    arquivos = [f for f in os.listdir(subpasta) if f.endswith(".csv")]
#    nome_pasta = os.path.basename(subpasta)  # Obtém o nome da pasta

#    for arquivo in arquivos:
#        caminho_arquivo = os.path.join(subpasta, arquivo)
#        try:
#            df = pd.read_csv(caminho_arquivo, encoding="utf-8", low_memory=False)  # Melhor para grandes volumes de dados
#            df["Arquivo_Origem"] = arquivo  # Adiciona o nome do arquivo de origem
#            df["Pasta_Origem"] = nome_pasta  # Adiciona o nome da pasta de origem
#            df_list.append(df)
#        except Exception as e:
#            print(f"Erro ao ler o arquivo {arquivo}: {e}")

#if df_list:
#    df_estoque = pd.concat(df_list, ignore_index=True)

#df_estoque['PDV'] = df_estoque['PDV'].astype(str)

#df_estoque['SKU_FINAL'] = np.where(df_estoque['SKU_PARA'] == "-", df_estoque['SKU'], df_estoque['SKU_PARA'])

#df_estoque['SKU_FINAL']=df_estoque['SKU_FINAL'].astype(str)'''


In [141]:
df_bi_preco = pd.read_excel(r"C:\Users\joao.herculano\GRUPO GINSENG\Assistência Suprimentos - 2025\SUPRIMENTOS\DB_PROMOÇÕES\EUDORA\202511\preço BI\TABELA DE PREÇOS (2).xlsx")

c:\Users\joao.herculano\AppData\Local\Programs\Python\Python313\Lib\site-packages\openpyxl\styles\stylesheet.py:237: UserWarning: Workbook contains no default style, apply openpyxl's default
  warn("Workbook contains no default style, apply openpyxl's default")


In [142]:
df_bi_preco.columns

Index(['SKU1', 'SKU2', 'Descrição', 'MARCA', 'CATEGORIA', 'LINHA', 'UF',
       'Tipo Preço', 'PC', 'PV'],
      dtype='object')

In [143]:
df_pdv = pd.read_excel(r"C:\Users\joao.herculano\Documents\PDV_ATT.xlsx")
df_pdv = df_pdv.rename(columns={'DESCRIÇÃO':'DESCRIÇÃO PDV'})
df_pdv = df_pdv.drop(columns=['REGIÃO', 'ESTADO','CIDADE','GESTÃO', 'SUPERVISOR', 'STATUS'])
df_pdv = df_pdv[~df_pdv['CANAL'].isin(['MTZ','LJ'])]




In [144]:
df_pdv['PDV'].value_counts()

PDV
20968    1
20969    1
20970    1
20986    1
20988    1
20989    1
20991    1
20992    1
20993    1
20994    1
20995    1
20996    1
20997    1
20998    1
20999    1
21000    1
21001    1
21278    1
21375    1
21383    1
21495    1
22448    1
22541    1
23703    1
23704    1
23711    1
23712    1
24255    1
24257    1
24269    1
24293    1
23813    1
Name: count, dtype: int64

In [145]:
df_pdv['MATCH'] = 1

**ALTERAR NOME DA COLUNA "ARQUIVO_ORIGEM" PARA UMA DAS OPÇÕES ABAIXO:**

*BOT.csv* 

*EUD.csv*

*QDB.csv*

In [146]:
#df_estoque = df_estoque[df_estoque['Arquivo_Origem']== "EUD.csv"]

In [147]:
calendario = pd.read_excel(r"C:\Users\joao.herculano\GRUPO GINSENG\Assistência Suprimentos - 2025\SUPRIMENTOS\BD_LANÇAMENTOS\BASE DE DADOS LANÇAMENTO\BOT\CICLO 9\CALENDARIO_CICLO\Ciclo_Expandido_com_Datas.xlsx")

In [148]:
calendario['Date'] = pd.to_datetime(calendario['Date'])

# Get today (normalized to midnight)
today = pd.Timestamp("today").normalize()

calendario['NUM_CICLO'] = calendario['Ciclo'].str[-2:].astype(int)
calendario['ANO_CICLO'] = calendario['Ciclo'].str[0:5]


calendario = calendario[calendario['MARCA'] == "EUDORA"]

calendario['CICLOMAIS2'] = calendario['ANO_CICLO'].astype(str) + (calendario['NUM_CICLO'].astype(int) + 2).astype(str).str.zfill(2)

ciclo_mais2 = calendario[calendario['Date'].dt.normalize() == today]['CICLOMAIS2'].iloc[0]


# Filter rows where date matches today
filtered_calendario = calendario[calendario['Ciclo'] == ciclo_mais2][:1]


filtered_calendario['dias_ate_inicio'] = filtered_calendario['INICIO CICLO'].iloc[0] - today

filtered_calendario['dias_ate_inicio'] = filtered_calendario['dias_ate_inicio'].dt.days.astype(int)



In [149]:
filtered_calendario

Ciclo INICIO CICLO  FIM CICLO  DURAÇÃO   MARCA       Date  NUM_CICLO  \
2388  C202514   2025-09-17 2025-10-07       21  EUDORA 2025-09-17         14   

     ANO_CICLO CICLOMAIS2  dias_ate_inicio  
2388     C2025    C202516               23

In [150]:
filtered_calendario['match'] = 1

In [151]:
df_pdv['UF'] = np.where(df_pdv['UF'] == 'VDC','BA',df_pdv['UF'])

In [152]:
df_tabela = pd.read_excel(r"C:\Users\joao.herculano\GRUPO GINSENG\Assistência Suprimentos - 2025\SUPRIMENTOS\DB_PROMOÇÕES\EUDORA\202513\tabela promo\TABELA-DE-PROMOS_C13-(1)-1752011522504.xlsx.xlsx",skiprows=1)


In [153]:
df_tabela.head()

Ciclo  Veiculo Tipo de Promoção Estratégia de Promoção    Tipo_mecanica  \
0  202513  Guia CF      Promoção CF        Movimentar Flow  Desconto Direto   
1  202513  Guia CF      Promoção CF        Movimentar Flow  Desconto Direto   
2  202513  Guia CF      Promoção CF        Movimentar Flow  Desconto Direto   
3  202513  Guia CF      Promoção CF        Movimentar Flow  Desconto Direto   
4  202513  Guia CF      Promoção CF        Movimentar Flow  Desconto Direto   

  Promo Período Limitado?  EAM       Categoria  Cód. Combo  Código do Item  \
0                     NaN  Não  PERF. FEMININA         NaN           85268   
1                     NaN  Não  PERF. FEMININA         NaN           93541   
2                     NaN  Não  PERF. FEMININA         NaN           53138   
3                     NaN  Não  PERF. FEMININA         NaN           50762   
4                     NaN  Não  PERF. FEMININA         NaN           49803   

   ... 0.34.2 0.35.2  0.2.3  0.25.3  0.28.3  0.3.3  0.32.3  0.34.3  0.35.3  \
0  ...  59.47  61.22    0.2    0.25    0.28    0.3    0.32    0.34    0.35   
1  ...  30.57  31.47    0.2    0.25    0.28    0.3    0.32    0.34    0.35   
2  ...  35.67  36.72    0.2    0.25    0.28    0.3    0.32    0.34    0.35   
3  ...  23.43  24.12    0.2    0.25    0.28    0.3    0.32    0.34    0.35   
4  ...  28.53  29.37    0.2    0.25    0.28    0.3    0.32    0.34    0.35   

   BSO  
0  Sim  
1  Sim  
2  Sim  
3  Sim  
4  Sim  

[5 rows x 47 columns]

In [154]:
df_tabela = df_tabela[[    'Ciclo',                 'Veiculo',
              'Tipo de Promoção',  'Estratégia de Promoção',
                 'Tipo_mecanica', 'Promo Período Limitado?',
                           'EAM',               'Categoria',
                    'Cód. Combo',          'Código do Item',
             'Descrição do Item',     'Chamada Promocional',
                 'Valor do Guia',      'Preço Promocionado',
                 '% de Desconto',           'RE compra por',
                  'RE Vende por',          'RE lucra  (R$)']]

In [155]:
df_tabela['Código do Item'] = df_tabela['Código do Item'].astype(str).str.replace(".0","",regex=False)

In [156]:
df_tabela.head()

Ciclo  Veiculo Tipo de Promoção Estratégia de Promoção    Tipo_mecanica  \
0  202513  Guia CF      Promoção CF        Movimentar Flow  Desconto Direto   
1  202513  Guia CF      Promoção CF        Movimentar Flow  Desconto Direto   
2  202513  Guia CF      Promoção CF        Movimentar Flow  Desconto Direto   
3  202513  Guia CF      Promoção CF        Movimentar Flow  Desconto Direto   
4  202513  Guia CF      Promoção CF        Movimentar Flow  Desconto Direto   

  Promo Período Limitado?  EAM       Categoria  Cód. Combo Código do Item  \
0                     NaN  Não  PERF. FEMININA         NaN          85268   
1                     NaN  Não  PERF. FEMININA         NaN          93541   
2                     NaN  Não  PERF. FEMININA         NaN          53138   
3                     NaN  Não  PERF. FEMININA         NaN          50762   
4                     NaN  Não  PERF. FEMININA         NaN          49803   

                                 Descrição do Item  \
0              EUDORA EAU DE PARFUM ROSÉ V2, 75 ml   
1        DIVA ESPLÊNDIDA DESODORANTE COLONIA 100ml   
2  EUDORA IMENSI DESODORANTE COLÔNIA SANCHO 100 ML   
3  EUDORA VELVET SENSUAL DESODORANTE COLÔNIA 100ML   
4                       CHIC DES COL RETRO 95ml V2   

                                 Chamada Promocional  Valor do Guia  \
0  EUDORA EAU DE PARFUM ROSÉ V2, 75 ml | DE R$234...          234.9   
1  FESTIVAL DE PERFUMARIA - ATÉ 40% OFF: DIVA ESP...          139.9   
2  FESTIVAL DE PERFUMARIA - ATÉ 40% OFF: EUDORA I...          149.9   
3  FESTIVAL DE PERFUMARIA - ATÉ 40% OFF: EUDORA V...          119.9   
4  FESTIVAL DE PERFUMARIA - ATÉ 40% OFF: CHIC DES...          119.9   

   Preço Promocionado  % de Desconto  RE compra por  RE Vende por  \
0               174.9          0.255         122.43         174.9   
1                89.9          0.357          62.93          89.9   
2               104.9          0.300          73.43         104.9   
3                68.9          0.425          48.23          68.9   
4                83.9          0.300          58.73          83.9   

   RE lucra  (R$)  
0           52.47  
1           26.97  
2           31.47  
3           20.67  
4           25.17

In [157]:
df_tabela = pd.merge(left=df_tabela,right=df0[['SKU','SKU_FINAL']],left_on='Código do Item',right_on='SKU',how='left')
df_tabela.head()

Ciclo  Veiculo Tipo de Promoção Estratégia de Promoção    Tipo_mecanica  \
0  202513  Guia CF      Promoção CF        Movimentar Flow  Desconto Direto   
1  202513  Guia CF      Promoção CF        Movimentar Flow  Desconto Direto   
2  202513  Guia CF      Promoção CF        Movimentar Flow  Desconto Direto   
3  202513  Guia CF      Promoção CF        Movimentar Flow  Desconto Direto   
4  202513  Guia CF      Promoção CF        Movimentar Flow  Desconto Direto   

  Promo Período Limitado?  EAM       Categoria  Cód. Combo Código do Item  \
0                     NaN  Não  PERF. FEMININA         NaN          85268   
1                     NaN  Não  PERF. FEMININA         NaN          85268   
2                     NaN  Não  PERF. FEMININA         NaN          85268   
3                     NaN  Não  PERF. FEMININA         NaN          85268   
4                     NaN  Não  PERF. FEMININA         NaN          85268   

                     Descrição do Item  \
0  EUDORA EAU DE PARFUM ROSÉ V2, 75 ml   
1  EUDORA EAU DE PARFUM ROSÉ V2, 75 ml   
2  EUDORA EAU DE PARFUM ROSÉ V2, 75 ml   
3  EUDORA EAU DE PARFUM ROSÉ V2, 75 ml   
4  EUDORA EAU DE PARFUM ROSÉ V2, 75 ml   

                                 Chamada Promocional  Valor do Guia  \
0  EUDORA EAU DE PARFUM ROSÉ V2, 75 ml | DE R$234...          234.9   
1  EUDORA EAU DE PARFUM ROSÉ V2, 75 ml | DE R$234...          234.9   
2  EUDORA EAU DE PARFUM ROSÉ V2, 75 ml | DE R$234...          234.9   
3  EUDORA EAU DE PARFUM ROSÉ V2, 75 ml | DE R$234...          234.9   
4  EUDORA EAU DE PARFUM ROSÉ V2, 75 ml | DE R$234...          234.9   

   Preço Promocionado  % de Desconto  RE compra por  RE Vende por  \
0               174.9          0.255         122.43         174.9   
1               174.9          0.255         122.43         174.9   
2               174.9          0.255         122.43         174.9   
3               174.9          0.255         122.43         174.9   
4               174.9          0.255         122.43         174.9   

   RE lucra  (R$)    SKU SKU_FINAL  
0           52.47  85268     56572  
1           52.47  85268     56572  
2           52.47  85268     56572  
3           52.47  85268     56572  
4           52.47  85268     56572

In [158]:
df_tabela['Código do Item'] = np.where(df_tabela['SKU_FINAL'].notna(),df_tabela['SKU_FINAL'],df_tabela['Código do Item'])

In [159]:
df_tabela = df_tabela.drop(columns=['SKU','SKU_FINAL'])

In [160]:
df_tabela.head()

Ciclo  Veiculo Tipo de Promoção Estratégia de Promoção    Tipo_mecanica  \
0  202513  Guia CF      Promoção CF        Movimentar Flow  Desconto Direto   
1  202513  Guia CF      Promoção CF        Movimentar Flow  Desconto Direto   
2  202513  Guia CF      Promoção CF        Movimentar Flow  Desconto Direto   
3  202513  Guia CF      Promoção CF        Movimentar Flow  Desconto Direto   
4  202513  Guia CF      Promoção CF        Movimentar Flow  Desconto Direto   

  Promo Período Limitado?  EAM       Categoria  Cód. Combo Código do Item  \
0                     NaN  Não  PERF. FEMININA         NaN          56572   
1                     NaN  Não  PERF. FEMININA         NaN          56572   
2                     NaN  Não  PERF. FEMININA         NaN          56572   
3                     NaN  Não  PERF. FEMININA         NaN          56572   
4                     NaN  Não  PERF. FEMININA         NaN          56572   

                     Descrição do Item  \
0  EUDORA EAU DE PARFUM ROSÉ V2, 75 ml   
1  EUDORA EAU DE PARFUM ROSÉ V2, 75 ml   
2  EUDORA EAU DE PARFUM ROSÉ V2, 75 ml   
3  EUDORA EAU DE PARFUM ROSÉ V2, 75 ml   
4  EUDORA EAU DE PARFUM ROSÉ V2, 75 ml   

                                 Chamada Promocional  Valor do Guia  \
0  EUDORA EAU DE PARFUM ROSÉ V2, 75 ml | DE R$234...          234.9   
1  EUDORA EAU DE PARFUM ROSÉ V2, 75 ml | DE R$234...          234.9   
2  EUDORA EAU DE PARFUM ROSÉ V2, 75 ml | DE R$234...          234.9   
3  EUDORA EAU DE PARFUM ROSÉ V2, 75 ml | DE R$234...          234.9   
4  EUDORA EAU DE PARFUM ROSÉ V2, 75 ml | DE R$234...          234.9   

   Preço Promocionado  % de Desconto  RE compra por  RE Vende por  \
0               174.9          0.255         122.43         174.9   
1               174.9          0.255         122.43         174.9   
2               174.9          0.255         122.43         174.9   
3               174.9          0.255         122.43         174.9   
4               174.9          0.255         122.43         174.9   

   RE lucra  (R$)  
0           52.47  
1           52.47  
2           52.47  
3           52.47  
4           52.47

In [161]:
df_tabela['MATCH'] = 1

In [162]:
df_tabela = pd.merge(left=df_tabela,right=df_pdv[['PDV','MATCH','UF','DESCRIÇÃO PDV','ANALISTA']],on='MATCH',how='inner')

In [163]:
df_tabela.head()

Ciclo  Veiculo Tipo de Promoção Estratégia de Promoção    Tipo_mecanica  \
0  202513  Guia CF      Promoção CF        Movimentar Flow  Desconto Direto   
1  202513  Guia CF      Promoção CF        Movimentar Flow  Desconto Direto   
2  202513  Guia CF      Promoção CF        Movimentar Flow  Desconto Direto   
3  202513  Guia CF      Promoção CF        Movimentar Flow  Desconto Direto   
4  202513  Guia CF      Promoção CF        Movimentar Flow  Desconto Direto   

  Promo Período Limitado?  EAM       Categoria  Cód. Combo Código do Item  \
0                     NaN  Não  PERF. FEMININA         NaN          56572   
1                     NaN  Não  PERF. FEMININA         NaN          56572   
2                     NaN  Não  PERF. FEMININA         NaN          56572   
3                     NaN  Não  PERF. FEMININA         NaN          56572   
4                     NaN  Não  PERF. FEMININA         NaN          56572   

   ... Preço Promocionado % de Desconto  RE compra por  RE Vende por  \
0  ...              174.9         0.255         122.43         174.9   
1  ...              174.9         0.255         122.43         174.9   
2  ...              174.9         0.255         122.43         174.9   
3  ...              174.9         0.255         122.43         174.9   
4  ...              174.9         0.255         122.43         174.9   

   RE lucra  (R$)  MATCH    PDV  UF      DESCRIÇÃO PDV  ANALISTA  
0           52.47      1  20968  SE   HIB ITABAIANINHA  MARCYARA  
1           52.47      1  20969  AL  HIB MARECHAL DEOD      HARY  
2           52.47      1  20970  BA   ER SAO SEBASTIAO    DARLIN  
3           52.47      1  20986  BA       HIB OLINDINA     LUCAS  
4           52.47      1  20988  BA      HIB QUEIMADAS    DARLIN  

[5 rows x 23 columns]

In [164]:
df_tabela = df_tabela.drop_duplicates()

In [165]:
df_tabela.columns

Index(['Ciclo', 'Veiculo', 'Tipo de Promoção', 'Estratégia de Promoção',
       'Tipo_mecanica', 'Promo Período Limitado?', 'EAM', 'Categoria',
       'Cód. Combo', 'Código do Item', 'Descrição do Item',
       'Chamada Promocional', 'Valor do Guia', 'Preço Promocionado',
       '% de Desconto', 'RE compra por', 'RE Vende por', 'RE lucra  (R$)',
       'MATCH', 'PDV', 'UF', 'DESCRIÇÃO PDV', 'ANALISTA'],
      dtype='object')

In [166]:
df.columns

Index(['pdv', 'SKU', 'SKU_FINAL', 'ESTOQUE ATUAL', 'ESTOQUE EM TRANSITO',
       'PEDIDO PENDENTE', 'Curva', 'CATEGORIA', 'DiasSemVenda',
       'nextcycleprojection', 'secondtonextcycleprojection'],
      dtype='object')

In [167]:
df.head()

pdv    SKU SKU_FINAL ESTOQUE ATUAL ESTOQUE EM TRANSITO PEDIDO PENDENTE  \
0  20968  47814     47814             3                   0               0   
1  20968  47888     47888            11                   0               0   
2  20968  49459     49459             0                   0               0   
3  20968  49543     49543             8                   0               0   
4  20968  50093     50093             0                   0               0   

  Curva            CATEGORIA  DiasSemVenda  nextcycleprojection  \
0     C         DESODORANTES            78                    3   
1     B  CUIDADOS COM A PELE            45                    4   
2     C            MAQUIAGEM           247                    0   
3     A           PERFUMARIA            32                    2   
4     E              CABELOS             0                    0   

   secondtonextcycleprojection  
0                            2  
1                            2  
2                            0  
3                            2  
4                            0

In [168]:
df['pdv'] = df['pdv'].astype(str)

In [169]:
df['SKU_FINAL'] = df['SKU_FINAL'].astype(str)


In [170]:
df_tabela['Código do Item'] = df_tabela['Código do Item'].astype('str')

In [171]:
df_tabela.columns

Index(['Ciclo', 'Veiculo', 'Tipo de Promoção', 'Estratégia de Promoção',
       'Tipo_mecanica', 'Promo Período Limitado?', 'EAM', 'Categoria',
       'Cód. Combo', 'Código do Item', 'Descrição do Item',
       'Chamada Promocional', 'Valor do Guia', 'Preço Promocionado',
       '% de Desconto', 'RE compra por', 'RE Vende por', 'RE lucra  (R$)',
       'MATCH', 'PDV', 'UF', 'DESCRIÇÃO PDV', 'ANALISTA'],
      dtype='object')

In [172]:
df_tabela['PDV'] = df_tabela['PDV'].astype(str)

In [173]:
df[['SKU_FINAL','pdv']].head()

SKU_FINAL    pdv
0     47814  20968
1     47888  20968
2     49459  20968
3     49543  20968
4     50093  20968

In [276]:
df[(df['SKU_FINAL']=='93403')]

pdv    SKU SKU_FINAL ESTOQUE ATUAL ESTOQUE EM TRANSITO  \
711    20968  93403     93403             1                   1   
1857   20969  93403     93403             0                   0   
5032   20991  93403     93403             5                   0   
5282   20992  93403     93403             0                   0   
7541   20995  93403     93403             0                   0   
8382   20996  93403     93403             1                  12   
10303  20997  93403     93403             9                   3   
10461  20998  93403     93403             4                  22   
13097  21278  93403     93403             5                   0   
13702  21495  93403     93403             2                   0   
14577  22541  93403     93403             0                   2   
18488  24255  93403     93403             1                   0   

      PEDIDO PENDENTE Curva CATEGORIA  DiasSemVenda  nextcycleprojection  \
711                 3     C  INFANTIL            18                    3   
1857                0     C  INFANTIL            53                    1   
5032                0     C  INFANTIL            60                    9   
5282                0     E  INFANTIL             0                   15   
7541                0     C  INFANTIL             4                    5   
8382               17     C  INFANTIL             3                   10   
10303               0     C  INFANTIL             2                   24   
10461              34     C  INFANTIL             2                   55   
13097               0     C  INFANTIL             2                   15   
13702               0     C  INFANTIL           111                    3   
14577               0     C  INFANTIL            81                    5   
18488               0     E  INFANTIL             0                   15   

       secondtonextcycleprojection  
711                              1  
1857                             0  
5032                             2  
5282                             3  
7541                             1  
8382                             2  
10303                            5  
10461                            9  
13097                            2  
13702                            1  
14577                            1  
18488                            3

In [174]:
df_final = pd.merge(left=df,right=df_tabela,right_on=['Código do Item','PDV'],left_on=['SKU_FINAL','pdv'],how='right')
df_final.shape  

(11606, 34)

In [175]:
df_final = pd.merge(left=df,right=df_tabela,right_on=['Código do Item','PDV'],left_on=['SKU','pdv'],how='right')

In [177]:
df_final.columns

Index(['pdv', 'SKU', 'SKU_FINAL', 'ESTOQUE ATUAL', 'ESTOQUE EM TRANSITO',
       'PEDIDO PENDENTE', 'Curva', 'CATEGORIA', 'DiasSemVenda',
       'nextcycleprojection', 'secondtonextcycleprojection', 'Ciclo',
       'Veiculo', 'Tipo de Promoção', 'Estratégia de Promoção',
       'Tipo_mecanica', 'Promo Período Limitado?', 'EAM', 'Categoria',
       'Cód. Combo', 'Código do Item', 'Descrição do Item',
       'Chamada Promocional', 'Valor do Guia', 'Preço Promocionado',
       '% de Desconto', 'RE compra por', 'RE Vende por', 'RE lucra  (R$)',
       'MATCH', 'PDV', 'UF', 'DESCRIÇÃO PDV', 'ANALISTA'],
      dtype='object')

In [178]:
df_final['pdv'] = df_final['PDV']
df_final['SKU_FINAL'] = df_final['Código do Item']

In [179]:
df_final['Descrição do Item']

0                      EUDORA EAU DE PARFUM ROSÉ V2, 75 ml
1                      EUDORA EAU DE PARFUM ROSÉ V2, 75 ml
2                      EUDORA EAU DE PARFUM ROSÉ V2, 75 ml
3                      EUDORA EAU DE PARFUM ROSÉ V2, 75 ml
4                      EUDORA EAU DE PARFUM ROSÉ V2, 75 ml
                               ...                        
10651    SIÀGE ELIXIR CAPILAR TRATAMENTO OVERNIGHT NUTR...
10652    SIÀGE ELIXIR CAPILAR TRATAMENTO OVERNIGHT NUTR...
10653    SIÀGE ELIXIR CAPILAR TRATAMENTO OVERNIGHT NUTR...
10654    SIÀGE ELIXIR CAPILAR TRATAMENTO OVERNIGHT NUTR...
10655    SIÀGE ELIXIR CAPILAR TRATAMENTO OVERNIGHT NUTR...
Name: Descrição do Item, Length: 10656, dtype: object

In [180]:
df_final.head(20)

pdv    SKU SKU_FINAL ESTOQUE ATUAL ESTOQUE EM TRANSITO PEDIDO PENDENTE  \
0   20968  56572     56572            35                   0            None   
1   20969  56572     56572            30                   0            None   
2   20970  56572     56572            81                   0            None   
3   20986  56572     56572            71                   0            None   
4   20988  56572     56572            51                   0            None   
5   20989  56572     56572            95                   0            None   
6   20991  56572     56572            35                   0            None   
7   20992  56572     56572           149                   0            None   
8   20993  56572     56572             0                 291            None   
9   20994  56572     56572           218                   0            None   
10  20995  56572     56572            55                   0            None   
11  20996  56572     56572            69                   0            None   
12  20997  56572     56572           231                   0            None   
13  20998  56572     56572           212                   0            None   
14  20999  56572     56572           127                   0            None   
15  21000  56572     56572            57                   0            None   
16  21001  56572     56572            70                   0            None   
17  21278  56572     56572            81                   0            None   
18  21375  56572     56572           107                   0            None   
19  21383  56572     56572            95                   0            None   

   Curva   CATEGORIA  DiasSemVenda  nextcycleprojection  ...  \
0      B  PERFUMARIA           0.0                  0.0  ...   
1      B  PERFUMARIA           0.0                  0.0  ...   
2      E  PERFUMARIA           0.0                  0.0  ...   
3      E  PERFUMARIA           0.0                  0.0  ...   
4      E  PERFUMARIA           0.0                  0.0  ...   
5      E  PERFUMARIA           0.0                  0.0  ...   
6      B  PERFUMARIA           0.0                  0.0  ...   
7      E  PERFUMARIA           0.0                  0.0  ...   
8      E  PERFUMARIA           0.0                  0.0  ...   
9      E  PERFUMARIA           0.0                  0.0  ...   
10     B  PERFUMARIA           0.0                  0.0  ...   
11     B  PERFUMARIA           0.0                  0.0  ...   
12     B  PERFUMARIA           0.0                  0.0  ...   
13     B  PERFUMARIA           0.0                  0.0  ...   
14     E  PERFUMARIA           0.0                  0.0  ...   
15     E  PERFUMARIA           0.0                  0.0  ...   
16     E  PERFUMARIA           0.0                  0.0  ...   
17     B  PERFUMARIA           0.0                  0.0  ...   
18     E  PERFUMARIA           0.0                  0.0  ...   
19     E  PERFUMARIA           0.0                  0.0  ...   

    Preço Promocionado  % de Desconto RE compra por RE Vende por  \
0                174.9          0.255        122.43        174.9   
1                174.9          0.255        122.43        174.9   
2                174.9          0.255        122.43        174.9   
3                174.9          0.255        122.43        174.9   
4                174.9          0.255        122.43        174.9   
5                174.9          0.255        122.43        174.9   
6                174.9          0.255        122.43        174.9   
7                174.9          0.255        122.43        174.9   
8                174.9          0.255        122.43        174.9   
9                174.9          0.255        122.43        174.9   
10               174.9          0.255        122.43        174.9   
11               174.9          0.255        122.43        174.9   
12               174.9          0.255        122.43        174.9   
13               174.9      

In [181]:
df_final['match'] = 1

In [182]:
df_final = pd.merge(left=df_final, right=filtered_calendario[['Ciclo','INICIO CICLO','FIM CICLO','DURAÇÃO','match','dias_ate_inicio']], on='match',how='inner')
df_final.shape

(10656, 40)

In [183]:
df_final.PDV.value_counts()

PDV
20968    333
20969    333
20970    333
20986    333
20988    333
20989    333
20991    333
20992    333
20993    333
20994    333
20995    333
20996    333
20997    333
20998    333
20999    333
21000    333
21001    333
21278    333
21375    333
21383    333
21495    333
22448    333
22541    333
23703    333
23704    333
23711    333
23712    333
24255    333
24257    333
24269    333
24293    333
23813    333
Name: count, dtype: int64

In [184]:
#df_final = pd.merge(left=df_final,right=df_pdv[['PDV', 'CANAL', 'DESCRIÇÃO PDV', 'PDV DESC','UF', 'MARCA', 'ANALISTA']],on = 'PDV',how='inner')
df_final.shape

(10656, 40)

In [185]:
#df_final['SKU'] = df_final['SKU'].astype(str) 
#df_final['PDV'] = df_final['PDV'].astype(str) 
#df_final = pd.merge(left=df_final,right=df_estoque[['SKU_FINAL', 'DDV PREVISTO', 'COBERTURA ATUAL','PDV']],right_on=['PDV','SKU_FINAL'],left_on=['PDV','SKU'],how='left')
#df_final.shape

In [186]:

r'''df_bi_preco['SKU2'] = df_bi_preco['SKU2'].astype(str).str.replace('.0','',regex=False) 

df_final = pd.merge(left=df_final,right=df_bi_preco[['SKU2', 'UF','Tipo Preço', 'PC', 'PV']],right_on=['UF','SKU2'],left_on=['UF','SKU_FINAL'],how='left')
df_final.shape  ''' 

"df_bi_preco['SKU2'] = df_bi_preco['SKU2'].astype(str).str.replace('.0','',regex=False) \n\ndf_final = pd.merge(left=df_final,right=df_bi_preco[['SKU2', 'UF','Tipo Preço', 'PC', 'PV']],right_on=['UF','SKU2'],left_on=['UF','SKU_FINAL'],how='left')\ndf_final.shape  "

In [187]:
df_final['pdv'].value_counts()

pdv
20968    333
20969    333
20970    333
20986    333
20988    333
20989    333
20991    333
20992    333
20993    333
20994    333
20995    333
20996    333
20997    333
20998    333
20999    333
21000    333
21001    333
21278    333
21375    333
21383    333
21495    333
22448    333
22541    333
23703    333
23704    333
23711    333
23712    333
24255    333
24257    333
24269    333
24293    333
23813    333
Name: count, dtype: int64

In [188]:
#df_bi_preco['SKU1'] = df_bi_preco['SKU1'].astype(str).str.replace('.0','',regex=False) 

#df_final = pd.merge(left=df_final,right=df_bi_preco[['SKU1', 'SKU2', 'UF', 'PC', 'PV']],right_on=['UF','SKU1'],left_on=['UF','SKU'],how='left')
#df_final.shape   

In [189]:
#df_bi_preco = df_bi_preco[df_bi_preco['MARCA']=='EUDORA']

In [190]:
#df_final['PRECO DE COMPRA'] = np.where(~df_final['PC_x'].isna(),df_final['PC_x'],df_final['PC_y'])

#df_final['PRECO DE VENDA'] = np.where(~df_final['PV_x'].isna(),df_final['PV_x'],df_final['PV_y'])



In [191]:
#df_estoque = df_estoque.rename(columns={'SKU_FINAL':'SKU_PARA_VALIDACAO'})
#df_final = pd.merge( left= df_final, right = df_estoque[['SKU_PARA_VALIDACAO','Arquivo_Origem']], left_on= 'SKU', right_on='SKU_PARA_VALIDACAO', how='left')

In [192]:
df_final.columns

Index(['pdv', 'SKU', 'SKU_FINAL', 'ESTOQUE ATUAL', 'ESTOQUE EM TRANSITO',
       'PEDIDO PENDENTE', 'Curva', 'CATEGORIA', 'DiasSemVenda',
       'nextcycleprojection', 'secondtonextcycleprojection', 'Ciclo_x',
       'Veiculo', 'Tipo de Promoção', 'Estratégia de Promoção',
       'Tipo_mecanica', 'Promo Período Limitado?', 'EAM', 'Categoria',
       'Cód. Combo', 'Código do Item', 'Descrição do Item',
       'Chamada Promocional', 'Valor do Guia', 'Preço Promocionado',
       '% de Desconto', 'RE compra por', 'RE Vende por', 'RE lucra  (R$)',
       'MATCH', 'PDV', 'UF', 'DESCRIÇÃO PDV', 'ANALISTA', 'match', 'Ciclo_y',
       'INICIO CICLO', 'FIM CICLO', 'DURAÇÃO', 'dias_ate_inicio'],
      dtype='object')

In [193]:
#df_final = df_final.drop(columns=['Desativação','Lançamento','Promoção Próximo Ciclo','Compra inteligente semanal/Sugestão de compra','Planograma','Carteira Bloqueada Para Novos Pedidos','Preço Sell In','Quantidade','Item analisado','Promoção Próximo Ciclo + 1','SKU_PARA_VALIDACAO','Ciclo_y'])

In [194]:
df_final['PDV_SKU'] = df_final['PDV'].astype(str) + df_final['SKU_FINAL'].astype(str) 
df_final['UFPRODUTO'] = df_final['UF'].astype(str) + df_final['SKU_FINAL'].astype(str)

df_final.shape

(10656, 42)

In [195]:
df_final['PDV']

0        20968
1        20969
2        20970
3        20986
4        20988
         ...  
10651    24255
10652    24257
10653    24269
10654    24293
10655    23813
Name: PDV, Length: 10656, dtype: object

In [196]:
df_final['nextcycleprojection'].value_counts()

df_final['secondtonextcycleprojection'].value_counts()

secondtonextcycleprojection
0.0      1603
1.0      1102
2.0       738
4.0       566
3.0       478
         ... 
368.0       1
141.0       1
105.0       1
310.0       1
231.0       1
Name: count, Length: 145, dtype: int64

In [197]:
#df_final['PROJEÇÃO DO CICLO PROMOCIONADO'] =df_final['Projeção Próximo Ciclo + 1'] - df_final['Projeção Próximo Ciclo'] # projeção do ciclo em estudo

In [198]:
#df_final['PROJEÇÃO DO CICLO PROMOCIONADO'].value_counts()

In [199]:
#df_final['Data Prevista Regularização'] = df_final['Data Prevista Regularização'].astype(str).replace('0','REGULAR')

In [200]:
df_final = df_final.rename(columns={'Arquivo_Origem': 'MARCA'})

In [201]:
#df_final = df_final[~df_final['MARCA'].isna()]
#df_final['MARCA'].isna().sum()

In [202]:
df_final = df_final.drop_duplicates()
df_final.shape

(10656, 42)

In [203]:
df_final.columns

Index(['pdv', 'SKU', 'SKU_FINAL', 'ESTOQUE ATUAL', 'ESTOQUE EM TRANSITO',
       'PEDIDO PENDENTE', 'Curva', 'CATEGORIA', 'DiasSemVenda',
       'nextcycleprojection', 'secondtonextcycleprojection', 'Ciclo_x',
       'Veiculo', 'Tipo de Promoção', 'Estratégia de Promoção',
       'Tipo_mecanica', 'Promo Período Limitado?', 'EAM', 'Categoria',
       'Cód. Combo', 'Código do Item', 'Descrição do Item',
       'Chamada Promocional', 'Valor do Guia', 'Preço Promocionado',
       '% de Desconto', 'RE compra por', 'RE Vende por', 'RE lucra  (R$)',
       'MATCH', 'PDV', 'UF', 'DESCRIÇÃO PDV', 'ANALISTA', 'match', 'Ciclo_y',
       'INICIO CICLO', 'FIM CICLO', 'DURAÇÃO', 'dias_ate_inicio', 'PDV_SKU',
       'UFPRODUTO'],
      dtype='object')

In [204]:
df_vendas['PDV'] = df_vendas['PDV'].astype(str)
df_vendas['SKU'] = df_vendas['SKU'].astype(str)

df_vendas.columns

Index(['PDV', 'SKU', 'DESCRICAO', 'C202411', 'C202412', 'C202413', 'C202414',
       'C202415', 'C202416', 'C202417', 'C202501', 'C202502', 'C202503',
       'C202504', 'C202505', 'C202506', 'C202507', 'C202508', 'C202509',
       'C202510', 'C202511', 'C202512'],
      dtype='object')

In [205]:
df_final.shape

(10656, 42)

In [206]:
df_vendas.head()

PDV   SKU                            DESCRICAO  C202411  C202412  \
0  11201  1004        FLORATTA DES COL MY BLUE 75ml      0.0      0.0   
1  11201  1005     DEM FLORATTA DES COL MY BLUE 4ml      0.0      0.0   
2  11201  1078      MATCH SRUM CAP POS QUIMICA 50ml      0.0      0.0   
3  11201  1296  PMPCK THE BLEND DES ANTIT AER 2x75g      0.0      0.0   
4  11201  1302       PMPCK LILY DES ANTIT AER 2x75g      0.0      0.0   

   C202413  C202414  C202415  C202416  C202417  ...  C202503  C202504  \
0      0.0      0.0      0.0      0.0      0.0  ...      0.0      0.0   
1      0.0      0.0      0.0      0.0      0.0  ...      0.0      0.0   
2      0.0      0.0      0.0      0.0      0.0  ...      0.0      0.0   
3      0.0      0.0      0.0      0.0      0.0  ...      0.0      0.0   
4      0.0      0.0      0.0      0.0      0.0  ...      0.0      0.0   

   C202505  C202506  C202507  C202508  C202509  C202510  C202511  C202512  
0      0.0      0.0      0.0      0.0      0.0      0.0      0.0      0.0  
1      0.0      0.0      0.0      0.0      0.0      0.0      0.0      0.0  
2      0.0      0.0      0.0      0.0      0.0      0.0      0.0      0.0  
3      0.0      0.0      0.0      0.0      0.0      0.0      0.0      0.0  
4      0.0      0.0      0.0      0.0      0.0      0.0      0.0      0.0  

[5 rows x 22 columns]

In [207]:
df_final = pd.merge(df_final,df_vendas,left_on=['PDV','SKU'],right_on=['PDV','SKU'],how='left')

In [208]:
df_final.columns

Index(['pdv', 'SKU', 'SKU_FINAL', 'ESTOQUE ATUAL', 'ESTOQUE EM TRANSITO',
       'PEDIDO PENDENTE', 'Curva', 'CATEGORIA', 'DiasSemVenda',
       'nextcycleprojection', 'secondtonextcycleprojection', 'Ciclo_x',
       'Veiculo', 'Tipo de Promoção', 'Estratégia de Promoção',
       'Tipo_mecanica', 'Promo Período Limitado?', 'EAM', 'Categoria',
       'Cód. Combo', 'Código do Item', 'Descrição do Item',
       'Chamada Promocional', 'Valor do Guia', 'Preço Promocionado',
       '% de Desconto', 'RE compra por', 'RE Vende por', 'RE lucra  (R$)',
       'MATCH', 'PDV', 'UF', 'DESCRIÇÃO PDV', 'ANALISTA', 'match', 'Ciclo_y',
       'INICIO CICLO', 'FIM CICLO', 'DURAÇÃO', 'dias_ate_inicio', 'PDV_SKU',
       'UFPRODUTO', 'DESCRICAO', 'C202411', 'C202412', 'C202413', 'C202414',
       'C202415', 'C202416', 'C202417', 'C202501', 'C202502', 'C202503',
       'C202504', 'C202505', 'C202506', 'C202507', 'C202508', 'C202509',
       'C202510', 'C202511', 'C202512'],
      dtype='object')

In [209]:
df_final.iloc[:, -18:-1] = df_final.iloc[:, -18:-1].fillna(0)

In [210]:
# Define list of target columns
sales_2024_cols = df_final.columns[-18:-1]
# Create a new column with the row-wise max
df_final['PICO DE VENDAS 17CICLOS'] = df_final[sales_2024_cols].max(axis=1)



In [211]:
df_final.head()

pdv    SKU SKU_FINAL ESTOQUE ATUAL ESTOQUE EM TRANSITO PEDIDO PENDENTE  \
0  20968  56572     56572            35                   0            None   
1  20969  56572     56572            30                   0            None   
2  20970  56572     56572            81                   0            None   
3  20986  56572     56572            71                   0            None   
4  20988  56572     56572            51                   0            None   

  Curva   CATEGORIA  DiasSemVenda  nextcycleprojection  ...  C202504  C202505  \
0     B  PERFUMARIA           0.0                  0.0  ...      0.0      9.0   
1     B  PERFUMARIA           0.0                  0.0  ...      2.0     37.0   
2     E  PERFUMARIA           0.0                  0.0  ...      0.0      0.0   
3     E  PERFUMARIA           0.0                  0.0  ...      0.0      0.0   
4     E  PERFUMARIA           0.0                  0.0  ...      0.0      0.0   

  C202506 C202507 C202508 C202509 C202510 C202511 C202512  \
0     4.0    14.0     0.0     0.0     1.0     0.0     0.0   
1    34.0    14.0     3.0     2.0     4.0     1.0     0.0   
2     0.0     0.0     0.0     0.0     0.0     0.0     NaN   
3     0.0     0.0     0.0     0.0     0.0     0.0     0.0   
4     0.0     0.0     0.0     0.0     0.0     0.0     0.0   

   PICO DE VENDAS 17CICLOS  
0                     38.0  
1                     37.0  
2                      0.0  
3                      0.0  
4                      0.0  

[5 rows x 63 columns]

In [212]:
df_final.PDV.value_counts()

PDV
20968    348
20991    348
20995    348
20996    348
20997    348
20998    348
21278    348
20969    347
22541    347
21495    346
20992    333
20986    333
20993    333
20989    333
20988    333
20970    333
21000    333
20999    333
20994    333
21001    333
21383    333
21375    333
22448    333
23703    333
23704    333
23711    333
23712    333
24255    333
24257    333
24269    333
24293    333
23813    333
Name: count, dtype: int64

In [213]:
sales_2024_cols

Index(['C202412', 'C202413', 'C202414', 'C202415', 'C202416', 'C202417',
       'C202501', 'C202502', 'C202503', 'C202504', 'C202505', 'C202506',
       'C202507', 'C202508', 'C202509', 'C202510', 'C202511'],
      dtype='object')

In [214]:
vendas_6_meses = df_final.columns[-8:-2]

df_final['Pico Vendas Ultimos 6 ciclos'] = df_final[vendas_6_meses].max(axis=1)

In [215]:
df_final.columns[-19]

'C202413'

In [216]:
CRESCIMENTO = (df_final[df_final.columns[-18]].sum() - df_final[df_final.columns[-3]].sum())/df_final[df_final.columns[-18]].sum() 
print(CRESCIMENTO)

df_final['CRESCIMENTO'] = .2

0.22600883356755672


In [217]:
mesmo_ciclo_ano_passado = df_final.columns[-19]
ciclo_ano_passado = df_final.columns[-19:-18].str.split(" ")[0][-1]
df_final[ciclo_ano_passado] = df_final[mesmo_ciclo_ano_passado]

In [218]:
df_final.columns[-19:-18].str.split(" ")[0][-1]

'C202414'

In [219]:
df_final.columns[-21:-3]

Index(['C202412', 'C202413', 'C202414', 'C202415', 'C202416', 'C202417',
       'C202501', 'C202502', 'C202503', 'C202504', 'C202505', 'C202506',
       'C202507', 'C202508', 'C202509', 'C202510', 'C202511', 'C202512'],
      dtype='object')

In [220]:
vendas_todos_historicos = df_final.columns[-21:-3]

df_final['MEDIANA DO HISTÓRICO'] = df_final[vendas_todos_historicos].median(axis=1)

df_final['MEDIA DO HISTÓRICO'] = df_final[vendas_todos_historicos].mean(axis=1)

df_final['MEDIANA DO HISTÓRICO'] = np.where(df_final['MEDIANA DO HISTÓRICO'] <1,df_final['MEDIA DO HISTÓRICO'],df_final['MEDIANA DO HISTÓRICO'])


In [221]:
CRESCIMENTO

np.float64(0.22600883356755672)

In [222]:
df_final['PV GINSENG'] = np.where(df_final['CRESCIMENTO'] * df_final[ciclo_ano_passado] + df_final[ciclo_ano_passado] < df_final['MEDIANA DO HISTÓRICO'],
                                    np.ceil(df_final['CRESCIMENTO'] * df_final['MEDIANA DO HISTÓRICO']+ df_final['MEDIANA DO HISTÓRICO']), 
                                    np.ceil(df_final['CRESCIMENTO']*df_final[ciclo_ano_passado]+df_final[ciclo_ano_passado]))

In [223]:
#df_final['PV GINSENG'] = np.where(df_final['PV GINSENG']<1, df_final['Projeção Próximo Ciclo + 1'],df_final['PV GINSENG'])

In [224]:
#df_final = df_final.rename(columns={df_final.columns[18]: "C-4", df_final.columns[19]: "C-3",df_final.columns[20]: "C-2",df_final.columns[21]: "C-1"})

In [225]:
df_final.columns

Index(['pdv', 'SKU', 'SKU_FINAL', 'ESTOQUE ATUAL', 'ESTOQUE EM TRANSITO',
       'PEDIDO PENDENTE', 'Curva', 'CATEGORIA', 'DiasSemVenda',
       'nextcycleprojection', 'secondtonextcycleprojection', 'Ciclo_x',
       'Veiculo', 'Tipo de Promoção', 'Estratégia de Promoção',
       'Tipo_mecanica', 'Promo Período Limitado?', 'EAM', 'Categoria',
       'Cód. Combo', 'Código do Item', 'Descrição do Item',
       'Chamada Promocional', 'Valor do Guia', 'Preço Promocionado',
       '% de Desconto', 'RE compra por', 'RE Vende por', 'RE lucra  (R$)',
       'MATCH', 'PDV', 'UF', 'DESCRIÇÃO PDV', 'ANALISTA', 'match', 'Ciclo_y',
       'INICIO CICLO', 'FIM CICLO', 'DURAÇÃO', 'dias_ate_inicio', 'PDV_SKU',
       'UFPRODUTO', 'DESCRICAO', 'C202411', 'C202412', 'C202413', 'C202414',
       'C202415', 'C202416', 'C202417', 'C202501', 'C202502', 'C202503',
       'C202504', 'C202505', 'C202506', 'C202507', 'C202508', 'C202509',
       'C202510', 'C202511', 'C202512', 'PICO DE VENDAS 17CICLOS',
      

In [226]:
df_final.drop(columns=df_final.columns[-21:-10], inplace=True)

df_final.drop(columns=df_final.columns[-13:-11], inplace=True)


In [227]:
# List all columns except the two
cols_to_group_by = df_final.columns.difference(['DDV PREVISTO', 'COBERTURA ATUAL'])

# Group and aggregate
df_final_dedup = df_final
   

In [228]:
#df_final['Compra inteligente Próximo Ciclo']


In [229]:
#df_final['DDV PREVISTO'] = df_final['DDV PREVISTO'].fillna(0.01)


In [230]:
#df_final_dedup['DDV PREVISTO'] = np.where(
#    df_final_dedup['DDV PREVISTO'] == 0,
#    0.01,
#    df_final_dedup['DDV PREVISTO']
#)


In [231]:
#df_final_dedup['DDV PREVISTO'].value_counts()

In [232]:
#df_final_dedup['EST PROJE FINAL CICLO ATUAL'] = (df_final_dedup['Estoque Atual'] + df_final_dedup['Estoque em Transito']) - round(df_final_dedup['dias_ate_inicio'] * df_final_dedup['DDV PREVISTO'],0)

In [233]:
#df_final_dedup['EST PROJE FINAL CICLO ATUAL'] = np.where(df_final_dedup['EST PROJE FINAL CICLO ATUAL']<0,0,df_final_dedup['EST PROJE FINAL CICLO ATUAL'])

In [234]:
#df_final_dedup.columns

In [235]:
#df_final_dedup['VENDAS R$ PV GINSENG'] = df_final_dedup['PRECO DE VENDA'] * df_final_dedup['PV GINSENG']

In [236]:
#df_final_dedup = df_final_dedup.rename(columns={'Ciclo_x':'Ciclo'})

In [237]:
df_final_dedup['SUGESTÃO ABTASTECIMENTO	'] = ''
df_final_dedup['VENDAS R$ ABASTECIMENTO'] = ''


In [238]:
#df_final_dedup['RBV 202406'] = df_final_dedup['PRECO DE VENDA'] * df_final_dedup[ciclo_ano_passado] 

In [239]:
#df_final_dedup['COB PROJETADA'] = np.where(
#    df_final_dedup['DDV PREVISTO'] != 0,
#    (df_final_dedup['EST PROJE FINAL CICLO ATUAL'] + df_final_dedup['PV GINSENG']) / df_final_dedup['DDV PREVISTO'],
#    999)


In [240]:
#df_final_dedup.drop(columns=['dias_ate_inicio','SKU_FINAL','Projeção Próximo Ciclo + 1',
#                             'CRESCIMENTO'],inplace=True)

In [241]:
#df_final_dedup['MARCA'] = df_final_dedup['MARCA'].str.replace('.csv','',regex=False)

In [242]:
#df_final_dedup['COB PROJETADA'] = df_final_dedup['COB PROJETADA'].fillna(999)

In [243]:
#df_final_dedup.columns

In [244]:
#marca_promo =  df_estoque['Arquivo_Origem'].iloc[0].replace('.csv','')
#marca_promo

In [245]:
df_final.columns

Index(['pdv', 'SKU', 'SKU_FINAL', 'ESTOQUE ATUAL', 'ESTOQUE EM TRANSITO',
       'PEDIDO PENDENTE', 'Curva', 'CATEGORIA', 'DiasSemVenda',
       'nextcycleprojection', 'secondtonextcycleprojection', 'Ciclo_x',
       'Veiculo', 'Tipo de Promoção', 'Estratégia de Promoção',
       'Tipo_mecanica', 'Promo Período Limitado?', 'EAM', 'Categoria',
       'Cód. Combo', 'Código do Item', 'Descrição do Item',
       'Chamada Promocional', 'Valor do Guia', 'Preço Promocionado',
       '% de Desconto', 'RE compra por', 'RE Vende por', 'RE lucra  (R$)',
       'MATCH', 'PDV', 'UF', 'DESCRIÇÃO PDV', 'ANALISTA', 'match', 'Ciclo_y',
       'INICIO CICLO', 'FIM CICLO', 'DURAÇÃO', 'dias_ate_inicio', 'PDV_SKU',
       'UFPRODUTO', 'DESCRICAO', 'C202411', 'C202414', 'C202509', 'C202510',
       'C202511', 'C202512', 'PICO DE VENDAS 17CICLOS',
       'Pico Vendas Ultimos 6 ciclos', 'CRESCIMENTO', 'MEDIANA DO HISTÓRICO',
       'MEDIA DO HISTÓRICO', 'PV GINSENG', 'SUGESTÃO ABTASTECIMENTO\t',
       'VENDA

In [246]:
# Passo 1: ordenar
df_sorted = df_final.sort_values(by='% de Desconto', ascending=False)

# Passo 2: obter até 3 chamadas promocionais por grupo
promo_grouped = (
    df_sorted.groupby(['SKU_FINAL', 'PDV'])['Chamada Promocional']
    .apply(lambda x: x.dropna().unique()[:3])
    .apply(pd.Series)
    .rename(columns={0: 'MECÂNICA 1', 1: 'MECÂNICA 2', 2: 'MECÂNICA 3'})
    .reset_index()
)

# Passo 3: base com maior % de desconto
df_base = df_sorted.drop_duplicates(subset=['SKU_FINAL', 'PDV'], keep='first').reset_index(drop=True)

# Passo 4: merge com chamadas pivotadas
df_merged = df_base.merge(promo_grouped, on=['SKU_FINAL', 'PDV'], how='left')

# Corrigir dicionário: agrupar e pegar o primeiro valor válido por (SKU_FINAL, PDV)
# Passo 1: dicionário com Cód. Combo único por SKU_FINAL+PDV
cod_combo_map = (
    df_final
    .dropna(subset=['Cód. Combo'])
    .groupby(['SKU_FINAL', 'PDV'])['Cód. Combo']
    .first()
    .to_dict()
)

# Passo 2: gerar Series com os valores mapeados
cod_combo_series = df_merged.set_index(['SKU_FINAL', 'pdv']).index.map(cod_combo_map)

# Passo 3: substituir os valores diretamente
df_merged['Cód. Combo'] = cod_combo_series.where(cod_combo_series.notna(), df_merged['Cód. Combo'])



In [247]:
df_merged.PDV.value_counts()

PDV
21375    270
21383    270
21495    270
22448    270
22541    270
23703    270
20969    270
20968    270
23704    270
23711    270
20999    270
21000    270
20994    270
20993    270
20995    270
20996    270
20997    270
20998    270
20986    270
20970    270
20991    270
20992    270
20989    270
20988    270
21001    270
21278    270
23813    270
24293    270
24269    270
24257    270
24255    270
23712    270
Name: count, dtype: int64

# Columns to bring up front
priority_cols = [
    'PDV_SKU',	'SKU',	'MARCA','INICIO CICLO',
    'FIM CICLO',	'DURAÇÃO','dias_ate_inicio',	
    'UFPRODUTO',	'Item Desativado',	'Data Prevista Regularização',
    'ANALISTA',	'UF',	'PDV',	'DESCRIÇÃO PDV',	'Classe',
    'Descrição','MECÂNICA 1',
       'MECÂNICA 2', 'MECÂNICA 3','Estoque Atual',	'COBERTURA ATUAL',
    'Estoque em Transito',	'Pedido Pendente',	'PICO DE VENDAS 2024','Pico Vendas Ultimos 6 ciclos',
    'C-4',	'C-3',	'C-2',	'C-1',	'Histórico de Vendas do Ciclo Atual',
    'Dias sem venda'
]

# All remaining columns
other_cols = [col for col in df_merged.columns if col not in priority_cols]

# Reorder
df_merged = df_merged[priority_cols + other_cols]


In [248]:
df_merged['INICIO CICLO'] = pd.to_datetime(df_merged['INICIO CICLO'], dayfirst=True).dt.strftime('%d/%m/%Y')

df_merged['FIM CICLO'] = pd.to_datetime(df_merged['FIM CICLO'], dayfirst=True).dt.strftime('%d/%m/%Y')

In [249]:
df_merged.columns

Index(['pdv', 'SKU', 'SKU_FINAL', 'ESTOQUE ATUAL', 'ESTOQUE EM TRANSITO',
       'PEDIDO PENDENTE', 'Curva', 'CATEGORIA', 'DiasSemVenda',
       'nextcycleprojection', 'secondtonextcycleprojection', 'Ciclo_x',
       'Veiculo', 'Tipo de Promoção', 'Estratégia de Promoção',
       'Tipo_mecanica', 'Promo Período Limitado?', 'EAM', 'Categoria',
       'Cód. Combo', 'Código do Item', 'Descrição do Item',
       'Chamada Promocional', 'Valor do Guia', 'Preço Promocionado',
       '% de Desconto', 'RE compra por', 'RE Vende por', 'RE lucra  (R$)',
       'MATCH', 'PDV', 'UF', 'DESCRIÇÃO PDV', 'ANALISTA', 'match', 'Ciclo_y',
       'INICIO CICLO', 'FIM CICLO', 'DURAÇÃO', 'dias_ate_inicio', 'PDV_SKU',
       'UFPRODUTO', 'DESCRICAO', 'C202411', 'C202414', 'C202509', 'C202510',
       'C202511', 'C202512', 'PICO DE VENDAS 17CICLOS',
       'Pico Vendas Ultimos 6 ciclos', 'CRESCIMENTO', 'MEDIANA DO HISTÓRICO',
       'MEDIA DO HISTÓRICO', 'PV GINSENG', 'SUGESTÃO ABTASTECIMENTO\t',
       'VENDA

In [250]:
df_merged = df_merged.loc[:, ~df_merged.columns.str.endswith('_y')]


In [251]:
df_merged.columns = df_merged.columns.str.replace('_x$', '', regex=True)


In [252]:
df_merged['DESCRICAO'] = df_merged['Descrição do Item']

In [253]:
df_merged['SKU'] = np.where(df_merged['SKU'].isna(),df_merged['SKU_FINAL'],df_merged['SKU'])

In [254]:
df_merged = df_merged.drop(columns=['Veiculo',	'Tipo de Promoção',	'Estratégia de Promoção','Tipo_mecanica'
                                    ,'Chamada Promocional','MATCH','match','Descrição do Item','CRESCIMENTO',
                                    'Cód. Combo'])

In [255]:
df_merged = df_merged.drop(columns=['Código do Item','PDV','RE compra por',	'RE Vende por',	'RE lucra  (R$)','INICIO CICLO',
                                    'FIM CICLO','Ciclo','CATEGORIA','ANALISTA','dias_ate_inicio','PDV_SKU','UFPRODUTO',
                                    'VENDAS R$ ABASTECIMENTO','DURAÇÃO','MEDIANA DO HISTÓRICO','DURAÇÃO'])

In [256]:
df_merged = df_merged.rename(columns={'nextcycleprojection':'PROJEÇÃO PROX CICLO'	,'secondtonextcycleprojection':'PROJEÇÃO PROX CICLO +1'})

In [257]:
df_merged.columns = df_merged.columns.str.upper()

In [258]:
#df_merged = df_merged[['UF','PDV','DESCRIÇÃO PDV','SKU','DESCRICAO','EAM','CATEGORIA','CURVA','ESTOQUE ATUAL','ESTOQUE EM TRANSITO','PEDIDO PENDENTE','DIASSEMVENDA','PROJEÇÃO PROX CICLO','PROJEÇÃO PROX CICLO +1','PROMO PERÍODO LIMITADO?','VALOR DO GUIA','PREÇO PROMOCIONADO','% DE DESCONTO','PICO DE VENDAS 17CICLOS','PICO VENDAS ULTIMOS 6 CICLOS','MEDIA DO HISTÓRICO']]

In [259]:
df_merged['MEDIA DO HISTÓRICO'] = round(df_merged['MEDIA DO HISTÓRICO'],0)

In [260]:
df_merged.columns

Index(['PDV', 'SKU', 'SKU_FINAL', 'ESTOQUE ATUAL', 'ESTOQUE EM TRANSITO',
       'PEDIDO PENDENTE', 'CURVA', 'DIASSEMVENDA', 'PROJEÇÃO PROX CICLO',
       'PROJEÇÃO PROX CICLO +1', 'PROMO PERÍODO LIMITADO?', 'EAM', 'CATEGORIA',
       'VALOR DO GUIA', 'PREÇO PROMOCIONADO', '% DE DESCONTO', 'UF',
       'DESCRIÇÃO PDV', 'DESCRICAO', 'C202411', 'C202414', 'C202509',
       'C202510', 'C202511', 'C202512', 'PICO DE VENDAS 17CICLOS',
       'PICO VENDAS ULTIMOS 6 CICLOS', 'MEDIA DO HISTÓRICO', 'PV GINSENG',
       'SUGESTÃO ABTASTECIMENTO\t', 'MECÂNICA 1', 'MECÂNICA 2', 'MECÂNICA 3'],
      dtype='object')

In [261]:
df_merged['SUGESTÃO COMERCIAL'] =""

In [262]:
# Colunas que devem estar na frente
colunas_inicio = [
    'UF', 'PDV', 'DESCRIÇÃO PDV', 'SKU', 'DESCRICAO', 'EAM', 'CATEGORIA', 'CURVA',
    'ESTOQUE ATUAL', 'ESTOQUE EM TRANSITO', 'PEDIDO PENDENTE', 'DIASSEMVENDA',
    'PROJEÇÃO PROX CICLO', 'PROJEÇÃO PROX CICLO +1', 'PROMO PERÍODO LIMITADO?',
    'VALOR DO GUIA', 'PREÇO PROMOCIONADO', '% DE DESCONTO',
    'PICO DE VENDAS 17CICLOS', 'PICO VENDAS ULTIMOS 6 CICLOS', 'MEDIA DO HISTÓRICO'
]

# Colunas que devem estar no fim
colunas_fim = [
    'PV GINSENG', 'SUGESTÃO ABTASTECIMENTO\t',  'SUGESTÃO COMERCIAL'
]

# Todas as outras colunas (não estão nem no início nem no fim)
colunas_meio = [col for col in df_merged.columns if col not in colunas_inicio + colunas_fim]

# Reordena o DataFrame
df_merged = df_merged[colunas_inicio + colunas_meio + colunas_fim]


In [263]:
df_merged = df_merged.drop_duplicates()

In [264]:

from openpyxl import load_workbook
from openpyxl.styles import PatternFill, Font


# Export to Excel
output_file = f'C:\\Users\\joao.herculano\\Documents\\EUD_promoção_{ciclo_mais2}_25.08.xlsx'
with pd.ExcelWriter(output_file, engine='openpyxl') as writer:
    df_merged.to_excel(writer, index=False, sheet_name='Sheet1')

# Apply styles
wb = load_workbook(output_file)
ws = wb['Sheet1']

# Style header
header_fill = PatternFill(start_color='ADD8E6', end_color='ADD8E6', fill_type='solid')  # Light Blue
header_font = Font(color='FFFFFF', bold=True)  # White & Bold

for cell in ws[1]:
    cell.fill = header_fill
    cell.font = header_font

# Style rows: gray/white alternating
gray_fill = PatternFill(start_color='DDDDDD', end_color='DDDDDD', fill_type='solid')  # Light gray

for i, row in enumerate(ws.iter_rows(min_row=2, max_row=ws.max_row), start=2):
    if i % 2 == 0:
        for cell in row:
            cell.fill = gray_fill

# Save styled workbook
wb.save(output_file)


coisas q saem

Lançamento
Subcategoria
Projeção Próximo Ciclo 
Promoção Próximo Ciclo
Compra inteligente semanal/Sugestão de compra
Compra inteligente Próximo Ciclo
Planograma
Carteira Bloqueada Para Novos Pedidos
Quantidade por caixa
Preço Sell In
Quantidade
Item analisado
Tipo Preço

>>>>>>>>>>>>>NAO ESTÁ PEGANDO O MERGE COM O DF_ESTOQUE


CRIAR PROJEÇÃO DE VENDA DO CICLO ATUAL
Compra inteligente Próximo Ciclo + 1 >>>>>>> RENAME PRA NOROMAL